In [1]:
import networkx as nx
from gerrychain import Graph
import math
import gurobipy as gp
from gurobipy import GRB

#import matplotlib.pyplot as plt
from util import update_attributes, get_k_L_U
from sketch import sketch
from detail import detail
from clusterings import clusterings

filepath1 = 'C:\\districting-data-2020\\'
filepath2 = 'C:\\districting-data-2020-conn\\'

In [2]:
# calculated in enacted_splits.ipynb
enacted_splits = {('AK', 'CD'): 0, ('AL', 'CD'): 6, ('AR', 'CD'): 3, ('AZ', 'CD'): 15, ('CA', 'CD'): 72, ('CO', 'CD'): 20, ('CT', 'CD'): 10, ('DE', 'CD'): 0, ('FL', 'CD'): 31, ('GA', 'CD'): 21, ('HI', 'CD'): 1, ('IA', 'CD'): 0, ('ID', 'CD'): 1, ('IL', 'CD'): 53, ('IN', 'CD'): 8, ('KS', 'CD'): 4, ('KY', 'CD'): 6, ('LA', 'CD'): 15, ('MA', 'CD'): 22, ('MD', 'CD'): 9, ('ME', 'CD'): 1, ('MI', 'CD'): 21, ('MN', 'CD'): 12, ('MO', 'CD'): 10, ('MS', 'CD'): 4, ('MT', 'CD'): 1, ('NC', 'CD'): 13, ('ND', 'CD'): 0, ('NE', 'CD'): 2, ('NH', 'CD'): 5, ('NJ', 'CD'): 20, ('NM', 'CD'): 10, ('NV', 'CD'): 5, ('NY', 'CD'): 26, ('OH', 'CD'): 14, ('OK', 'CD'): 7, ('OR', 'CD'): 16, ('PA', 'CD'): 17, ('RI', 'CD'): 1, ('SC', 'CD'): 10, ('SD', 'CD'): 0, ('TN', 'CD'): 11, ('TX', 'CD'): 59, ('UT', 'CD'): 7, ('VA', 'CD'): 11, ('VT', 'CD'): 0, ('WA', 'CD'): 11, ('WI', 'CD'): 13, ('WV', 'CD'): 0, ('WY', 'CD'): 0, ('AK', 'SS'): 19, ('AL', 'SS'): 35, ('AR', 'SS'): 51, ('AZ', 'SS'): 44, ('CA', 'SS'): 56, ('CO', 'SS'): 42, ('CT', 'SS'): 49, ('DE', 'SS'): 20, ('FL', 'SS'): 32, ('GA', 'SS'): 60, ('HI', 'SS'): 21, ('IA', 'SS'): 46, ('ID', 'SS'): 25, ('IL', 'SS'): 135, ('IN', 'SS'): 48, ('KS', 'SS'): 36, ('KY', 'SS'): 21, ('LA', 'SS'): 77, ('MA', 'SS'): 59, ('MD', 'SS'): 45, ('ME', 'SS'): 40, ('MI', 'SS'): 64, ('MN', 'SS'): 100, ('MO', 'SS'): 16, ('MS', 'SS'): 64, ('MT', 'SS'): 56, ('NC', 'SS'): 24, ('ND', 'SS'): 49, ('NE', 'SS'): 37, ('NH', 'SS'): 40, ('NJ', 'SS'): 56, ('NM', 'SS'): 64, ('NV', 'SS'): 21, ('NY', 'SS'): 66, ('OH', 'SS'): 20, ('OK', 'SS'): 59, ('OR', 'SS'): 47, ('PA', 'SS'): 47, ('RI', 'SS'): 41, ('SC', 'SS'): 68, ('SD', 'SS'): 29, ('TN', 'SS'): 15, ('TX', 'SS'): 41, ('UT', 'SS'): 41, ('VA', 'SS'): 34, ('VT', 'SS'): 18, ('WA', 'SS'): 59, ('WI', 'SS'): 73, ('WV', 'SS'): 13, ('WY', 'SS'): 25, ('AK', 'SH'): 39, ('AL', 'SH'): 115, ('AR', 'SH'): 128, ('AZ', 'SH'): 44, ('CA', 'SH'): 95, ('CO', 'SH'): 73, ('CT', 'SH'): 162, ('DE', 'SH'): 40, ('FL', 'SH'): 112, ('GA', 'SH'): 209, ('HI', 'SH'): 47, ('IA', 'SH'): 92, ('ID', 'SH'): 25, ('IL', 'SH'): 220, ('IN', 'SH'): 129, ('KS', 'SH'): 127, ('KY', 'SH'): 80, ('LA', 'SH'): 116, ('MA', 'SH'): 182, ('MD', 'SH'): 67, ('ME', 'SH'): 166, ('MI', 'SH'): 154, ('MN', 'SH'): 176, ('MO', 'SH'): 137, ('MS', 'SH'): 181, ('MT', 'SH'): 99, ('NC', 'SH'): 80, ('ND', 'SH'): 53, ('NH', 'SH'): 154, ('NJ', 'SH'): 56, ('NM', 'SH'): 86, ('NV', 'SH'): 43, ('NY', 'SH'): 179, ('OH', 'SH'): 77, ('OK', 'SH'): 134, ('OR', 'SH'): 79, ('PA', 'SH'): 186, ('RI', 'SH'): 75, ('SC', 'SH'): 145, ('SD', 'SH'): 31, ('TN', 'SH'): 74, ('TX', 'SH'): 101, ('UT', 'SH'): 72, ('VA', 'SH'): 98, ('VT', 'SH'): 118, ('WA', 'SH'): 59, ('WI', 'SH'): 159, ('WV', 'SH'): 89, ('WY', 'SH'): 56}


In [3]:
def number_of_county_splits(districts_geoid):
    county_geoids = { geoid[0:5] for district in districts_geoid for geoid in district }
    county_assignment = { county_geoid : list() for county_geoid in county_geoids }
    for j in range(len(districts_geoid)):
        for geoid in districts_geoid[j]:
            county_geoid = geoid[0:5]
            if j not in county_assignment[county_geoid]:
                county_assignment[county_geoid].append(j)
    return sum( len(county_assignment[cg]) - 1 for cg in county_assignment.keys() )

In [4]:
import csv

def export_to_baf(geoid_assignment, outfilename):
    
    with open(outfilename, 'w') as csvfile: 
        csvwriter = csv.writer(csvfile) 
        for i in GB.nodes:
            geoid = GB.nodes[i]['GEOID20']
            county = geoid[0:5]
            tract = geoid[0:11]
            block = geoid
            if county in geoid_assignment:
                row = [geoid, geoid_assignment[county]+1]
            elif tract in geoid_assignment:
                row = [geoid, geoid_assignment[tract]+1]
            else:
                row = [geoid, geoid_assignment[block]+1]
            csvwriter.writerow(row) 
    
    return

In [5]:
from number_of_districts import congressional_districts_2020
states = sorted([ state for state in congressional_districts_2020.keys() ])

results = dict()
instances = list( clusterings.keys() )
instances.reverse()

for (state, district_type) in instances: 

    print("**********************************")
    print("State:",state,"district_type:",district_type)
    print("**********************************")

    # get county graph
    filename = state + '_county.json'
    GC = Graph.from_json( filepath1 + filename )
    update_attributes(GC, state)    

    # get tract graph
    filename = state + '_tract.json'
    GT = Graph.from_json( filepath2 + filename )
    update_attributes(GT, state)    

    # get block graph
    filename = state + '_block.json'
    GB = Graph.from_json( filepath2 + filename )
    update_attributes(GB, state)    

    # get values of k, L, U; check connectivity
    (k, L, U) = get_k_L_U(GC, state, district_type)
    if k <= 1 or not nx.is_connected(GC) or not nx.is_connected(GT) or not nx.is_connected(GB):
        print("Skipping this state because k <= 1 or because graph is disconnected.")
        continue

    clusters = clusterings[state,district_type]['clusters'] 
    sizes = clusterings[state,district_type]['sizes'] 
    districts = list()

    for p in range(len(clusters)):

        cluster = clusters[p]
        size = sizes[p]
        GS = GC.subgraph(cluster)
        
        print("size =",size)
        print("cluster =",cluster)
        print("population = ",[ GS.nodes[i]['TOTPOP'] for i in GS.nodes ] )
        print("L,U =",L,U)

        ################################
        # get a sketch for this cluster
        ################################
        
        (xsoln, ysoln, zsoln) = sketch(GS, L, U, size)
        if xsoln is None:
            print("Sketch indicates that this cluster is infeasible; impossible to get k-1 splits!!!")
            districts = None
            break

        ################################
        # visualize this cluster
        ################################
        
#         node_pos = { i : ( GS.nodes[i]['X'], GS.nodes[i]['Y'] ) for i in GS.nodes }
#         node_colors = [ list(xsoln[i])[0] for i in GS.nodes ]
#         edge_colors = [ list(ysoln[u,v])[0] if len(ysoln[u,v]) > 0 else -1 for u,v in GS.edges ]

#         title = state + '_' + district_type
#         plt.figure(title)
#         my_labels = { i : list(xsoln[i].keys()) for i in GS.nodes }
#         nx.draw(GS, pos=node_pos, node_color=node_colors, edge_color=edge_colors, with_labels=True, labels=my_labels, font_color="red")
#         plt.show()

        #########################
        # detail this cluster
        #########################
        
        # first, try tract-level
        sketch_support = { GS.nodes[i]['GEOID20'] : list(xsoln[i].keys()) for i in GS.nodes }
        tracts = [ i for i in GT.nodes if GT.nodes[i]['GEOID20'][0:5] in sketch_support.keys() ]
        cluster_districts = detail(GT.subgraph(tracts), L, U, size, sketch_support)
        cluster_districts_geoid = None # just the initial value!

        if cluster_districts is not None:
            cluster_districts_geoid = [ [ GT.nodes[i]['GEOID20'] for i in district ] for district in cluster_districts ]
        else:
            # second, try block-level
            blocks = [ i for i in GB.nodes if GB.nodes[i]['GEOID20'][0:5] in sketch_support.keys() ]
            cluster_districts = detail(GB.subgraph(blocks), L, U, size, sketch_support)
            if cluster_districts is not None:
                cluster_districts_geoid = [ [ GB.nodes[i]['GEOID20'] for i in district ] for district in cluster_districts ]

        # both tries unsuccessful?
        if cluster_districts_geoid is None:
            districts = None
            break
        else:
            districts += cluster_districts_geoid

    # all clusters successful?
    if districts is not None:
        assert k == len(districts)
        splits = number_of_county_splits(districts)
    else:
        districts_geoid = None
        splits = None

    # store results
    results[state,district_type] = dict()
    results[state,district_type]['clusters'] = clusters
    results[state,district_type]['num_clusters'] = len(sizes)
    results[state,district_type]['sizes'] = sizes
    results[state,district_type]['districts'] = districts
    results[state,district_type]['counties'] = GC.number_of_nodes()
    results[state,district_type]['k'] = k
    results[state,district_type]['L'] = f'{L:,d}'
    results[state,district_type]['U'] = f'{U:,d}'
    results[state,district_type]['obvious_LB'] = sum( math.ceil( GC.nodes[i]['TOTPOP'] / U ) - 1 for i in GC.nodes )
    results[state,district_type]['splits_LB'] = k - len(sizes)
    results[state,district_type]['splits_UB'] = splits
    
    # export districts to block assignment file
    if districts is not None:
        geoid_assignment = { g : j for j in range(len(districts)) for g in districts[j] }
        outfilename = "min_county_splits_" + state + '_' + district_type + "_(by_Maral_Shahmizad_and_Austin_Buchanan_of_Oklahoma_State_University).baf"
        export_to_baf(geoid_assignment, outfilename)  

**********************************
State: WV district_type: CD
**********************************
Starting WV with k = 2 and deviation = 0.01
Thus, we have L = 892374 and U = 901342
size = 1
cluster = [0, 1, 4, 8, 10, 12, 13, 15, 17, 18, 19, 22, 23, 26, 28, 29, 30, 31, 33, 34, 43, 45, 49, 50, 52, 54]
population =  [21382, 12447, 12376, 32977, 27932, 6143, 11959, 23816, 74591, 24604, 25453, 6229, 20463, 180745, 23568, 38982, 7869, 57440, 21809, 94350, 8378, 19111, 8051, 32567, 40488, 59664]
L,U = 892374 901342
Set parameter Username
Academic license - for non-commercial use only - expires 2024-01-27
size = 1
cluster = [2, 3, 5, 6, 7, 9, 11, 14, 16, 20, 21, 24, 25, 27, 32, 35, 36, 37, 38, 39, 40, 41, 42, 44, 46, 47, 48, 51, 53]
population =  [14028, 10976, 7808, 5194, 8313, 8444, 56205, 122076, 16705, 7408, 22559, 42425, 17063, 17033, 14442, 30591, 27791, 105822, 26938, 29095, 34216, 14299, 84296, 23093, 65921, 15465, 6762, 7653, 57701]
L,U = 892374 901342
*******************************

Trying DAG model, with roots = [1432, 1481]
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: Intel(R) Xeon(R) CPU E5-2630 v4 @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 10 physical cores, 20 logical processors, using up to 20 threads

Optimize a model with 1082 rows, 720 columns and 4806 nonzeros
Model fingerprint: 0xa1a2704a
Variable types: 185 continuous, 535 integer (535 binary)
Coefficient statistics:
  Matrix range     [1e+00, 8e+03]
  Objective range  [9e+03, 3e+08]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+05]
Presolve removed 900 rows and 603 columns
Presolve time: 0.01s
Presolved: 182 rows, 117 columns, 782 nonzeros
Variable types: 0 continuous, 117 integer (117 binary)
Found heuristic solution: objective 5.049368e+09

Explored 0 nodes (0 simplex iterations) in 0.03 seconds (0.01 work units)
Thread count was 20 (of 20 available processors)

Solution count 1: 5.04937e+09 

Optimal solution found (tolerance 1.00e-01)
Best ob

0 	 0.00 	 0.04
1 	 2632090886.66 	 0.02
2 	 976887043.49 	 0.01
3 	 770127679.00 	 0.01
4 	 745266155.01 	 0.01
5 	 738655463.92 	 0.01
6 	 736650103.88 	 0.01
7 	 736230343.79 	 0.00
8 	 736083259.83 	 0.01
9 	 736040399.02 	 0.00
10 	 736022088.95 	 0.00
11 	 736016857.80 	 0.00
12 	 736016428.23 	 0.00
13 	 736016428.23 	 0.00
Set parameter OutputFlag to value 1
Trying DAG model, with roots = [251, 4965, 523, 904, 577, 3671, 736]
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: Intel(R) Xeon(R) CPU E5-2630 v4 @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 10 physical cores, 20 logical processors, using up to 20 threads

Optimize a model with 9991 rows, 8736 columns and 57498 nonzeros
Model fingerprint: 0x4ea58f14
Variable types: 798 continuous, 7938 integer (7938 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+04]
  Objective range  [2e+02, 1e+08]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+05]
Presolve removed 1166 ro

Trying tract-level instance.
Iteration 	 Objective 	 iter_time
0 	 0.00 	 0.00
1 	 20486441085.05 	 0.00
2 	 20481120081.28 	 0.00
3 	 20481120081.28 	 0.00
Set parameter OutputFlag to value 1
Trying DAG model, with roots = [5208, 4457]
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: Intel(R) Xeon(R) CPU E5-2630 v4 @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 10 physical cores, 20 logical processors, using up to 20 threads

Optimize a model with 1061 rows, 706 columns and 4590 nonzeros
Model fingerprint: 0xdb1acdf0
Variable types: 165 continuous, 541 integer (541 binary)
Coefficient statistics:
  Matrix range     [1e+00, 2e+04]
  Objective range  [5e+01, 3e+09]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+05]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Presolve removed 863 rows and 585 columns
Presolve time: 0.02s
Presolved: 198 rows, 121 columns, 810 nonzeros
Variable ty

3 	 1689571618.02 	 0.00
4 	 1689534839.93 	 0.00
5 	 1689534839.93 	 0.00
Set parameter OutputFlag to value 1
Trying DAG model, with roots = [3281, 3577]
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: Intel(R) Xeon(R) CPU E5-2630 v4 @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 10 physical cores, 20 logical processors, using up to 20 threads

Optimize a model with 1001 rows, 666 columns and 4364 nonzeros
Model fingerprint: 0xf0efb7dd
Variable types: 113 continuous, 553 integer (553 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+04]
  Objective range  [1e+03, 1e+08]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+05]
Presolve removed 626 rows and 456 columns
Presolve time: 0.02s
Presolved: 375 rows, 210 columns, 1347 nonzeros
Variable types: 0 continuous, 210 integer (208 binary)

Root relaxation: objective 1.689535e+09, 1 iterations, 0.00 seconds (0.00 work units)

    Nodes    |    Current Node    |     Objective Bounds 

...

Found heuristic solution: objective 3.184417e+07

Explored 0 nodes (0 simplex iterations) in 0.03 seconds (0.00 work units)
Thread count was 20 (of 20 available processors)

Solution count 1: 3.18442e+07 

Optimal solution found (tolerance 1.00e-01)
Best objective 3.184416586454e+07, best bound 3.184416586454e+07, gap 0.0000%
**********************************
State: AK district_type: SH
**********************************
Starting AK with k = 40 and deviation = 0.1
Thus, we have L = 17419 and U = 19251
size = 1
cluster = [0]
population =  [18666]
L,U = 17419 19251
size = 6
cluster = [4, 19]
population =  [5343, 107081]
L,U = 17419 19251
Trying tract-level instance.
Iteration 	 Objective 	 iter_time
0 	 0.00 	 0.00
1 	 1126480663.68 	 0.00
2 	 1084907339.98 	 0.00
3 	 1082536162.26 	 0.00
4 	 1081341700.77 	 0.00
5 	 1081277732.85 	 0.00
6 	 1081277732.85 	 0.00
Set parameter OutputFlag to value 1
Trying DAG model, with roots = [15, 141, 66, 1, 144, 14]
Gurobi Optimizer version 10.0.1 b


Optimize a model with 1053 rows, 976 columns and 6464 nonzeros
Model fingerprint: 0x87663177
Variable types: 0 continuous, 976 integer (976 binary)
Coefficient statistics:
  Matrix range     [1e+00, 9e+03]
  Objective range  [6e+01, 2e+07]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 2e+04]
Presolve removed 782 rows and 706 columns
Presolve time: 0.05s
Presolved: 271 rows, 270 columns, 1369 nonzeros
Variable types: 0 continuous, 270 integer (270 binary)

Root relaxation: objective 8.773752e+06, 70 iterations, 0.00 seconds (0.00 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 8773751.90    0   21          - 8773751.90      -     -    0s
     0     0 9449168.85    0   47          - 9449168.85      -     -    0s
     0     0 9547448.33    0   47          - 9547448.33      -     -    0s
     0     0 9565571.76    0   47          - 9565571.76     


     0     0 4.0410e+09    0  146          - 4.0410e+09      -     -    3s
     0     0 4.0428e+09    0  697          - 4.0428e+09      -     -    9s
     0     0 4.0429e+09    0  623          - 4.0429e+09      -     -    9s
     0     0 4.0429e+09    0  626          - 4.0429e+09      -     -    9s
     0     0 4.0429e+09    0  627          - 4.0429e+09      -     -    9s
     0     0 4.0431e+09    0  657          - 4.0431e+09      -     -   10s
     0     0 4.0431e+09    0  654          - 4.0431e+09      -     -   10s
     0     0 4.0433e+09    0  601          - 4.0433e+09      -     -   11s
     0     0 4.0433e+09    0  603          - 4.0433e+09      -     -   11s
     0     0 4.0433e+09    0  667          - 4.0433e+09      -     -   12s
     0     0 4.0433e+09    0  675          - 4.0433e+09      -     -   12s
     0     0 4.0433e+09    0  657          - 4.0433e+09      -     -   12s
     0     0 4.0433e+09    0  544          - 4.0433e+09      -     -   13s
     0     2 4.0433e+09 

 468664 178647 5.5289e+07   31   25          - 5.1724e+07      -  13.2   55s
 510702 191525 1.2866e+08   32   32          - 5.2515e+07      -  13.2   60s
 551677 203399 7.1433e+07   31   30          - 5.3367e+07      -  13.3   65s
 596484 216416 1.0525e+08   29   21          - 5.4194e+07      -  13.4   70s
 640397 228734 infeasible   42               - 5.4936e+07      -  13.4   75s
 682679 241568 7.0956e+07   34   20          - 5.5617e+07      -  13.5   80s
 729574 255365 5.9215e+07   31   29          - 5.6276e+07      -  13.6   85s
 774899 267575 infeasible   34               - 5.6925e+07      -  13.6   90s
 811017 277764 6.4845e+07   27   35          - 5.7464e+07      -  13.7   95s
 853616 289914 infeasible   34               - 5.8006e+07      -  13.7  100s
 888712 300318 infeasible   46               - 5.8407e+07      -  13.7  105s
 936513 314020 9.3011e+07   28   28          - 5.8971e+07      -  13.8  110s
 974806 324769 8.0767e+07   38   14          - 5.9434e+07      -  13.8  115s

 4072450 881051 infeasible   38               - 8.4452e+07      -  15.0  585s
 4095897 883352 infeasible   47               - 8.4626e+07      -  15.0  590s
 4121673 885846 infeasible   32               - 8.4811e+07      -  15.0  595s
 4148766 888456 infeasible   29               - 8.5002e+07      -  15.0  600s

Cutting planes:
  Gomory: 3
  Cover: 608
  MIR: 48
  StrongCG: 37
  Flow cover: 3
  Inf proof: 20
  Zero half: 5
  RLT: 1
  Lazy constraints: 485

Explored 4148806 nodes (62164128 simplex iterations) in 600.03 seconds (251.69 work units)
Thread count was 20 (of 20 available processors)

Solution count 0

Time limit reached
Best objective -, best bound 8.500185248199e+07, gap -

User-callback calls 8446856, time in user-callback 27.70 sec
Trying block-level instance.
Iteration 	 Objective 	 iter_time
0 	 0.00 	 0.09
1 	 18224765.13 	 0.03
2 	 5521416.80 	 0.03
3 	 5428119.07 	 0.01
4 	 5421391.70 	 0.01
5 	 5420194.48 	 0.01
6 	 5419609.48 	 0.01
7 	 5419461.87 	 0.01
8 	 5419394

In [6]:
print("results =",results)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [7]:
print('state  district_type  splits_LB  splits_UB  gap')
for (state, district_type) in results.keys():
    splits_LB = results[state,district_type]['k'] - clusterings[state,district_type]['cluster_UB']
    splits_UB = results[state,district_type]['splits_UB'] 
    if splits_UB is None:
        print(state,district_type, splits_LB, splits_UB, 'None')
    else:
        print(state,district_type, splits_LB, splits_UB, splits_UB-splits_LB)

state  district_type  splits_LB  splits_UB  gap
WV CD 0 0 0
WI CD 1 1 0
WA CD 4 4 0
VA CD 2 2 0
UT CD 1 1 0
TX CD 19 19 0
TN CD 2 2 0
SC CD 1 1 0
RI CD 1 1 0
PA CD 7 None None
OR CD 1 1 0
OK CD 1 1 0
OH CD 4 4 0
NY CD 18 18 0
NV CD 2 2 0
NM CD 0 0 0
NJ CD 9 9 0
NH CD 1 1 0
NE CD 0 0 0
NC CD 3 3 0
MT CD 0 0 0
MS CD 0 0 0
MO CD 1 1 0
MN CD 2 2 0
MI CD 4 4 0
ME CD 0 0 0
MD CD 4 4 0
MA CD 7 7 0
LA CD 0 0 0
KY CD 1 1 0
KS CD 0 0 0
IN CD 1 1 0
IL CD 9 9 0
ID CD 0 0 0
IA CD 0 0 0
GA CD 2 2 0
FL CD 19 19 0
CT CD 4 4 0
CO CD 2 2 0
CA CD 41 41 0
AZ CD 7 7 0
AR CD 0 0 0
AL CD 0 0 0
WY SS 20 20 0
WV SS 4 4 0
WI SS 13 13 0
WA SS 36 36 0
VT SS 24 24 0
VA SS 16 16 0
UT SS 22 22 0
TX SS 12 12 0
TN SS 13 13 0
SD SS 19 19 0
SC SS 30 30 0
RI SS 35 35 0
PA SS 27 27 0
OR SS 19 19 0
OK SS 23 23 0
OH SS 13 13 0
NY SS 43 43 0
NV SS 18 18 0
NM SS 29 29 0
NJ SS 30 30 0
NH SS 20 20 0
NE SS 28 28 0
ND SS 29 29 0
NC SS 22 None None
MT SS 31 31 0
MS SS 23 23 0
MO SS 14 14 0
MN SS 41 41 0
MI SS 20 20 0
ME SS 27 27 0

In [8]:
for district_type in ['CD', 'SS', 'SH']:
    print("results for",district_type,":")
    print("state |C| k L U obvious_LB max_clusters split_LB min_splits enacted_splits")
    for state in states:
        if (state, district_type) in results.keys():
            s = state
            t = district_type
            print(state,end=' & ')
            print(results[s,t]['counties'],end=' & ')
            print(results[s,t]['k'],end=' & ')
            print(results[s,t]['L'],end=' & ')
            print(results[s,t]['U'],end=' & ')
            print(results[s,t]['obvious_LB'],end=' & ')
            print(results[s,t]['num_clusters'],end=' & ')
            print(results[s,t]['splits_LB'],end=' & ')
            print(results[s,t]['splits_UB'],end=' & ')
            print(enacted_splits[s,t],'\\\\')  
            
    print("\n\n")

results for CD :
state |C| k L U obvious_LB max_clusters split_LB min_splits enacted_splits
AL & 67 & 7 & 714,166 & 721,342 & 0 & 7 & 0 & 0 & 6 \\
AR & 75 & 4 & 749,117 & 756,645 & 0 & 4 & 0 & 0 & 3 \\
AZ & 15 & 9 & 790,639 & 798,584 & 6 & 2 & 7 & 7 & 15 \\
CA & 58 & 52 & 756,549 & 764,152 & 39 & 11 & 41 & 41 & 72 \\
CO & 64 & 8 & 718,106 & 725,322 & 1 & 6 & 2 & 2 & 20 \\
CT & 8 & 5 & 717,583 & 724,794 & 3 & 1 & 4 & 4 & 10 \\
FL & 67 & 28 & 765,375 & 773,067 & 10 & 9 & 19 & 19 & 31 \\
GA & 159 & 14 & 761,311 & 768,961 & 2 & 12 & 2 & 2 & 21 \\
IA & 99 & 4 & 793,605 & 801,580 & 0 & 4 & 0 & 0 & 0 \\
ID & 44 & 2 & 914,956 & 924,150 & 0 & 2 & 0 & 0 & 1 \\
IL & 102 & 17 & 749,909 & 757,445 & 7 & 8 & 9 & 9 & 53 \\
IN & 92 & 9 & 750,178 & 757,717 & 1 & 8 & 1 & 1 & 8 \\
KS & 105 & 4 & 730,798 & 738,142 & 0 & 4 & 0 & 0 & 4 \\
KY & 120 & 6 & 747,218 & 754,727 & 1 & 5 & 1 & 1 & 6 \\
LA & 64 & 6 & 772,412 & 780,174 & 0 & 6 & 0 & 0 & 15 \\
MA & 14 & 9 & 777,197 & 785,007 & 5 & 2 & 7 & 7 & 22 \\
MD &